<h1><center> Environment Classification</center></h1>

![](https://images.aicrowd.com/raw_images/challenges/banner_file/897/b4a0766bb1ef4b621e3a.jpg)

In this challenge, you will have images of a self driving car moving through a town in different weather conditions. Your goal will be to classify the environment into 5 different classes ( using unsupervised methonds ), 1 means the weather is really good for a self driving car while 5 means the weather is very challenging for a self driving car.

  - Unsupvised Image Classification

## Image clustering using Transfer learning 

### Resnet50 + Kmeans based image clustering model

https://towardsdatascience.com/image-clustering-using-transfer-learning-df5862779571

In [1]:
!pip install -q aicrowd-cli
%load_ext aicrowd.magic

     |████████████████████████████████| 43 kB 1.4 MB/s 
     |████████████████████████████████| 211 kB 5.8 MB/s 
     |████████████████████████████████| 54 kB 2.4 MB/s 
     |████████████████████████████████| 170 kB 42.4 MB/s 
     |████████████████████████████████| 62 kB 782 kB/s 
     |████████████████████████████████| 63 kB 1.6 MB/s 
     |████████████████████████████████| 51 kB 6.3 MB/s 
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
google-colab 1.0.0 requires requests~=2.23.0, but you have requests 2.26.0 which is incompatible.
datascience 0.10.6 requires folium==0.2.1, but you have folium 0.8.3 which is incompatible.


In [2]:
%aicrowd login

Please login here: https://api.aicrowd.com/auth/c6Qi0xWslXuXAsFmCs0kZaDCN5xR2f88RzqNFJV685A
API Key valid
Saved API Key successfully!


In [3]:
# Downloading the Dataset
!rm -rf data
!mkdir data
%aicrowd ds dl -c environment-classification -o data

images.zip:   0%|          | 0.00/22.8M [00:00<?, ?B/s]

In [4]:
# Unzipping and Organising the datasets
!unzip data/images.zip  -d data/images > /dev/null

In [5]:
import os
import csv 
from pathlib import Path
import random
import time

import pandas as pd
import numpy as np

In [6]:
DATA_DIR = "data/images/"

### Model 

In [7]:
from tensorflow.keras.applications.resnet50 import ResNet50
from tensorflow.keras.models import Sequential

resnet = ResNet50(include_top=False, pooling='avg', weights='imagenet')
my_new_model = Sequential()
my_new_model.add(resnet)

94781440/94765736 [==============================] - 1s 0us/step


In [8]:
# Say not to train first layer (ResNet) model. It is already trained
my_new_model.layers[0].trainable = False

### Images Preprocessing

In [9]:
%%time
from tensorflow.keras.applications.resnet50 import preprocess_input
import cv2 
import numpy as np

resnet_feature_list = []
images = [f for f in os.listdir(DATA_DIR)]
for image in images:
    file = DATA_DIR+image
    #print(file)
    im = cv2.imread(file)
    #im = cv2.resize(im,(256,256))
    img = preprocess_input(np.expand_dims(im.copy(), axis=0))
    resnet_feature = my_new_model.predict(img)
    resnet_feature_np = np.array(resnet_feature)
    resnet_feature_list.append(resnet_feature_np.flatten())

array = np.array(resnet_feature_list)

CPU times: user 1min 12s, sys: 2.51 s, total: 1min 14s
Wall time: 1min 39s


In [10]:
array.shape

(700, 2048)

### Training
https://scikit-learn.org/stable/modules/clustering.html

In [42]:
from sklearn.cluster import KMeans 

kmeans = KMeans(n_clusters=5, random_state=None).fit(array)  # 

print(kmeans.labels_)

[4 1 3 3 1 3 3 4 2 0 3 1 3 2 0 3 3 1 4 4 1 1 1 0 1 4 0 2 4 4 4 2 0 4 4 4 4
 0 3 0 3 3 1 3 3 0 1 3 1 0 4 1 4 3 0 3 4 1 1 3 0 3 3 1 2 4 1 2 4 0 4 1 1 4
 1 4 3 2 0 1 0 4 0 4 3 1 4 4 4 0 0 3 0 2 3 0 2 4 2 1 1 3 1 4 1 3 2 4 4 4 0
 2 3 1 4 3 4 4 1 4 4 4 1 0 1 4 0 3 4 4 0 0 0 4 4 3 1 1 0 1 1 0 4 4 3 3 1 3
 3 1 0 2 1 3 3 2 1 2 1 1 0 2 2 4 0 3 0 3 2 1 0 1 4 0 3 1 4 4 4 3 2 1 4 3 4
 1 3 3 1 1 1 1 4 1 2 4 0 2 0 0 2 0 2 1 2 1 3 1 3 1 0 3 0 3 4 0 2 3 4 1 2 3
 1 0 4 0 4 3 3 1 1 1 2 1 4 3 3 0 3 1 0 4 2 1 2 4 3 0 1 0 1 3 4 1 1 0 3 4 3
 4 2 1 1 3 2 4 0 3 4 4 1 2 1 2 2 3 1 2 1 2 3 3 4 1 1 4 1 0 0 1 1 1 4 4 3 3
 1 1 0 3 1 0 1 0 3 1 3 2 0 3 3 4 1 1 1 3 1 1 0 4 1 4 1 4 0 2 4 3 4 3 0 0 0
 0 3 4 3 2 4 2 4 1 4 1 1 2 1 4 0 1 4 1 2 2 4 4 0 0 1 4 2 4 1 4 1 1 3 1 3 1
 4 0 1 4 1 3 1 0 1 1 1 1 3 2 3 3 1 3 1 1 1 1 1 1 4 1 4 4 4 2 4 0 1 3 4 1 0
 4 3 1 3 0 2 4 2 1 1 3 4 3 3 0 1 4 4 1 4 3 1 4 4 1 3 0 0 1 4 3 4 1 3 4 0 2
 4 4 4 4 4 4 3 2 1 3 3 4 4 3 4 1 0 1 1 2 4 2 1 3 2 0 1 1 2 3 0 0 1 0 1 2 1
 0 1 3 0 4 4 3 1 4 0 4 4 

### Submission

In [43]:
img_ids_list = [f[:-4] for f in images]

In [44]:
images[0]

'95.jpg'

In [45]:
submission = {'ImageID':img_ids_list, "label":kmeans.labels_}
submission = pd.DataFrame(submission)

submission = submission.astype(int)
submission = submission.sort_values(by=['ImageID'])  

submission

ImageID  label
493        0      3
657        1      4
282        2      4
205        3      1
327        4      3
..       ...    ...
622      695      1
104      696      1
681      697      3
86       698      4
380      699      1

[700 rows x 2 columns]

In [46]:
submission.label.value_counts()

1    202
4    177
3    140
0    106
2     75
Name: label, dtype: int64

In [47]:
!rm -rf assets
!mkdir assets

submission.to_csv(os.path.join("assets", "submission.csv"), index=False)

## Making Direct Submission thought Aicrowd CLI

In [48]:
!aicrowd notebook submit -c environment-classification -a assets --no-verify

Using notebook: /content/drive/MyDrive/Colab Notebooks/BlitzXI_Resnet50_Kmeans_Cluster.ipynb for submission...
Removing existing files from submission directory...
Scrubbing API keys from the notebook...
submission.zip ━━━━━━━━━━━━━━━━━━━━━━ 100.0% • 23.2/21.5 KB • 2.3 MB/s • 0:00:00
                                                       ╭─────────────────────────╮                                                       
                                                       │ Successfully submitted! │                                                       
                                                       ╰─────────────────────────╯                                                       
                                                             Important links                                                             
┌──────────────────┬────────────────────────────────────────────────────────────────────────────────────────────────────────────────────┐
│  This submission │ http